# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [40]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [41]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("../Vacation_Search/WeatherPy_vacation.csv")

# Display sample data
vacation_df.head(10)

City_ID            City Country  Max Temp Current Description    Lat  \
0        3          Castro      BR     69.10     overcast clouds -24.79   
1        6       Busselton      AU     60.57          few clouds -33.65   
2        8         Rikitea      PF     72.23     overcast clouds -23.12   
3        9  Cabo San Lucas      MX     69.10          few clouds  22.89   
4       14         Shimoda      JP     57.11     overcast clouds  34.67   
5       27         Ahipara      NZ     58.78       broken clouds -35.17   
6       50         Ushuaia      AR     55.02       broken clouds -54.80   
7       54       Lixourion      GR     60.80       broken clouds  38.20   
8       73           Kapaa      US     71.92    scattered clouds  22.08   
9       74           Muros      ES     56.08     overcast clouds  42.78   

      Lng                     Hotel Name  
0  -50.01                   Grande Hotel  
1  115.33        Broadwater Beach Resort  
2 -134.97           Chez Bianca & Benoit  
3 -109.91            Hotel Estancia Real  
4  138.95                          黒船ホテル  
5  173.17                    YHA Ahipara  
6  -68.30   Apart Hotel Aires del Beagle  
7   20.43                       Palatino  
8 -159.32              Coral Reef Resort  
9   -9.06  Hotel-Restaurante La Muradana

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [42]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["City","Hotel Name","Country","Current Description"]
)

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [43]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"] == "Manhattan"]
vacation_end = vacation_df.loc[vacation_df["City"] =="Elizabeth City"]
vacation_stop1 = vacation_df.loc[vacation_df["City"] == "Jesup"]
vacation_stop2 = vacation_df.loc[vacation_df["City"] == "Pascagoula"]
vacation_stop3 = vacation_df.loc[vacation_df["City"] == "Manhattan"]

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [44]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
destinations = [vacation_start, vacation_end, vacation_stop1, vacation_stop2, vacation_stop3]

itinerary_df = pd.concat(destinations)

# Display sample data
itinerary_df

City_ID            City Country  Max Temp   Current Description    Lat  \
113      624       Manhattan      US     55.65            light rain  40.78   
15       118  Elizabeth City      US     62.02         moderate rain  36.29   
20       137           Jesup      US     66.13  heavy intensity rain  31.61   
55       320      Pascagoula      US     71.65      scattered clouds  30.37   
113      624       Manhattan      US     55.65            light rain  40.78   

       Lng      Hotel Name  
113 -73.97   La Quinta Inn  
15  -76.25     Quality Inn  
20  -81.89        Days Inn  
55  -88.56  Grand Magnolia  
113 -73.97   La Quinta Inn

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [45]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[["Lng","Lat"]].copy()

# Display sample data
waypoints_df

Lng    Lat
113 -73.97  40.78
15  -76.25  36.29
20  -81.89  31.61
55  -88.56  30.37
113 -73.97  40.78

## Use GeoViews to create map that shows the four cities in the itinerary

In [58]:
# Configure the map plot by using the itineraty_df
waypoints_map = itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    color="City",
    size = 100,
    frame_width = 400,
    frame_height = 400,
    alpha = 0.5)

In [59]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [60]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [61]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': '498d8d0844c145b6b09bc8d2fc406b60',
 'waypoints': '40.78,-73.97|36.29,-76.25|31.61,-81.89|30.37,-88.56|40.78,-73.97'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [62]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params=params)

# Convert the API response to JSON format
route_response = route_response.json()

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [63]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response["features"][0]["geometry"]["coordinates"]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [64]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for step in legs:
    for direction in step:
        lat = direction[1]
        lng = direction[0]
        longitude.append(lng)
        latitude.append(lat)

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [80]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df["Longitude"]=longitude
route_df["Latitude"]=latitude

# Display sample data
route_df.head()

Longitude   Latitude
0 -73.970245  40.779563
1 -73.970318  40.779587
2 -73.970452  40.779635
3 -73.970577  40.779686
4 -73.970689  40.779738

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [81]:
# Configure the route path by using the GeoViews' Path function
route_path = route_df.hvplot.paths(
    "Longitude",
    "Latitude",
    geo = True,
    tiles = "OSM",
    frame_width = 400,
    frame_height = 400,
    color = "red",
    line_width=3,
    alpha = 1
)

In [82]:
# Display a composed plot by using the route_map and route_path objects
route_path*itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    color="City",
    size = 100,
    frame_width = 400,
    frame_height = 400,
    alpha = 0.5)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Path.I   :Path   [Longitude,Latitude]
   .Points.I :Points   [Lng,Lat]   (City)